# Using GPT-2 for better Word embeddings #

In [36]:
from torch import nn
from transformers import BertModel, BertTokenizer
import json
from typing import List
import os
import numpy as np
import logging
from transformers import AdamW
import torch
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib as plt
import json, sklearn, pickle, sys, re, os
import IPython.display as ipd
from transformers import AutoTokenizer
from datasets import load_dataset
from datasets import ClassLabel
import random
from IPython.display import display, HTML
from transformers import AutoModelForCausalLM
from transformers import Trainer, TrainingArguments

In [2]:
torch.cuda.empty_cache()

In [3]:
#os.environ["CUDA_VISIBLE_DEVICES"]="0,1,2,3,4,5,6,7"

In [4]:
datapd=pd.read_json("/home/ubuntu/project/arxiv-metadata-oai-snapshot.json",  lines=True)

In [5]:
datapd_hep_th = datapd.loc[datapd['categories'].str.contains('hep-th')]
hep_abstracts = datapd_hep_th[ list(datapd_hep_th.iloc[:,0:1]) + ['abstract'] + ['title']+['authors']]

In [6]:
texttxt=hep_abstracts.abstract.values

In [7]:
texttxt[1]

'  We give a prescription for how to compute the Callias index, using as\nregulator an exponential function. We find agreement with old results in all\nodd dimensions. We show that the problem of computing the dimension of the\nmoduli space of self-dual strings can be formulated as an index problem in\neven-dimensional (loop-)space. We think that the regulator used in this Letter\ncan be applied to this index problem.\n'

Removing random \n that are present in the database

In [13]:
text_txt=[x.replace('\n',' ') for x in texttxt]
text_sep = [x.strip().split(".") for x in text_txt]
text_sep_fin = [x[:-1] for x in text_sep]

In [14]:
text_sep_fin[109345]

['First, I present two new classes of magnetic rotating solutions in four-dimensional Einstein-Maxwell-dilaton gravity with Liouville-type potential',
 ' The first class of solutions yields a 4-dimensional spacetime with a longitudinal magnetic field generated by a static or spinning magnetic string',
 ' I find that these solutions have no curvature singularity and no horizons, but have a conic geometry',
 ' In these spacetimes, when the rotation parameter does not vanish, there exists an electric field, and therefore the spinning string has a net electric charge which is proportional to the rotation parameter',
 ' The second class of solutions yields a spacetime with an angular magnetic field',
 ' These solutions have no curvature singularity, no horizon, and no conical singularity',
 ' The net electric charge of the strings in these spacetimes is proportional to their velocities',
 ' Second, I obtain the ($n+1$)-dimensional rotating solutions in Einstein-dilaton gravity with Liouvill

In [15]:
len(text_sep_fin[19345])

5

In [16]:
len(text_sep_fin)

140500

In [41]:
!pip install transformers

You should consider upgrading via the '/home/ubuntu/anaconda3/envs/pytorch_p36/bin/python -m pip install --upgrade pip' command.


In [42]:
!pip install datasets

You should consider upgrading via the '/home/ubuntu/anaconda3/envs/pytorch_p36/bin/python -m pip install --upgrade pip' command.


In [ ]:
random.shuffle(text_txt)
g=open("/home/ubuntu/arxiv.txt","w")
for x in text_txt:
    g.write(x)
    g.write("\n")
g.close()

In [ ]:
g=open("/home/ubuntu/arxivdev.txt","w")
for x in text_txt[10000:10500]:
    g.write(x)
    g.write("\n")
g.close()

In [17]:
datasets = load_dataset("text", data_files={"train": "/home/ubuntu/project/arxiv.txt","validation": "/home/ubuntu/project/arxiv_small_roberta.txt"})

Using custom data configuration default-7d64757c5d1f6c54
Reusing dataset text (/home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57)


In [18]:
print(datasets["train"][0])
print(datasets["validation"][0])

{'text': '  We study the dynamic collapse driven by a scalar field, when a relativistic observer falls co-moving with the collapse and cross the horizon of a Schwarzschild black-hole (BH), at $t=t_0$. During the collapse the scale of time is considered as variable. Back-reaction effects and gravitational waves produced during the exponential collapse are studied. We demonstrate that back-reaction effects act as the source of gravitational waves emitted during the collapse, and wavelengths of gravitational waves (GW) are in the range: $\\lambda \\ll r_s\\equiv {e^{-2h_0t_0}\\over 2 h_0}$, that is, smaller than the Schwarzschild radius. We demonstrate that during all the collapse the global topology of the space-time remains hyperbolic when the observer cross the horizon. '}
{'text': '  The problem of the gauge dependence of the fermion mass in the Maxwell-Chern-Simons QED$_{2+1}$ is revisited. Using Proca mass term as an intermediate infrared regulator we are demonstrating gauge-invaria

In [19]:
def show_random_elements(dataset, num_examples=10):
    assert num_examples <= len(dataset), "Can't pick more elements than there are in the dataset."
    picks = []
    for _ in range(num_examples):
        pick = random.randint(0, len(dataset)-1)
        while pick in picks:
            pick = random.randint(0, len(dataset)-1)
        picks.append(pick)
    
    df = pd.DataFrame(dataset[picks])
    for column, typ in dataset.features.items():
        if isinstance(typ, ClassLabel):
            df[column] = df[column].transform(lambda i: typ.names[i])
    display(HTML(df.to_html()))

In [20]:
show_random_elements(datasets["train"])

In [21]:
model_checkpoint = "gpt2-medium"

In [22]:
tokenizer = AutoTokenizer.from_pretrained(model_checkpoint, use_fast=True)

In [23]:
def tokenize_function(examples):
    return tokenizer(examples["text"])

In [24]:
tokenized_datasets = datasets.map(tokenize_function, batched=True, num_proc=4, remove_columns=["text"])

Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-160f36f162c7e428.arrow
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-47812fd83caad429.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-d7576edfd12700ac.arrow
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-23abb7d77182643e.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-d78be5f49dfe65b0.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-f2eff3fc7fad95b5.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-c8ccb2baee0256a3.arrow
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-50ba27850225c6f7.arrow


In [29]:
tokenized_datasets["train"].shape

(140500, 2)

In [30]:
block_size = 128

In [31]:
def group_texts(examples):
    concatenated_examples = {k: sum(examples[k], []) for k in examples.keys()}
    total_length = len(concatenated_examples[list(examples.keys())[0]])
    total_length = (total_length // block_size) * block_size
    result = {
        k: [t[i : i + block_size] for i in range(0, total_length, block_size)]
        for k, t in concatenated_examples.items()
    }
    result["labels"] = result["input_ids"].copy()
    return result

In [32]:
lm_datasets = tokenized_datasets.map(
    group_texts,
    batched=True,
    batch_size=128,
    num_proc=4)

Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-84988aeb1cd34472.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-fe3377e3e961b4e8.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-bdaf8663be3a54c9.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-3a139460f612d7e1.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-23a8343ac9d320c4.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-80d8025458d3b651.arrow
Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-1ff9bacca46f0c32.arrow


Loading cached processed dataset at /home/ubuntu/.cache/huggingface/datasets/text/default-7d64757c5d1f6c54/0.0.0/293ecb642f9fca45b44ad1f90c8445c54b9d80b95ab3fca3cfa5e1e3d85d4a57/cache-c421c1b741e98093.arrow


In [33]:
tokenizer.decode(lm_datasets["train"][0]["input_ids"])

'  We study the dynamic collapse driven by a scalar field, when a relativistic observer falls co-moving with the collapse and cross the horizon of a Schwarzschild black-hole (BH), at $t=t_0$. During the collapse the scale of time is considered as variable. Back-reaction effects and gravitational waves produced during the exponential collapse are studied. We demonstrate that back-reaction effects act as the source of gravitational waves emitted during the collapse, and wavelengths of gravitational waves (GW) are in the range: $\\lambda \\ll r_s\\equiv {e^{-2h_0'

In [38]:
model = AutoModelForCausalLM.from_pretrained(model_checkpoint,output_attentions=True,output_hidden_states=True)

In [40]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model= nn.DataParallel(model)
model.to(device)

DataParallel(
  (module): GPT2LMHeadModel(
    (transformer): GPT2Model(
      (wte): Embedding(50257, 1024)
      (wpe): Embedding(1024, 1024)
      (drop): Dropout(p=0.1, inplace=False)
      (h): ModuleList(
        (0): Block(
          (ln_1): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (attn): Attention(
            (c_attn): Conv1D()
            (c_proj): Conv1D()
            (attn_dropout): Dropout(p=0.1, inplace=False)
            (resid_dropout): Dropout(p=0.1, inplace=False)
          )
          (ln_2): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (mlp): MLP(
            (c_fc): Conv1D()
            (c_proj): Conv1D()
            (dropout): Dropout(p=0.1, inplace=False)
          )
        )
        (1): Block(
          (ln_1): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (attn): Attention(
            (c_attn): Conv1D()
            (c_proj): Conv1D()
            (attn_dropout): Dropout(p=0.1, inplace=False)
    

In [41]:
training_args = TrainingArguments(
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    weight_decay=0.01,
    output_dir="./gpt2",
    num_train_epochs=1,logging_steps=500, save_steps=500,  overwrite_output_dir=True,
    per_device_train_batch_size=8
)

In [42]:
trainer = Trainer(
    model=model.module,
    args=training_args,
    train_dataset=lm_datasets["train"],
    eval_dataset=lm_datasets["validation"])

In [43]:
torch.cuda.empty_cache()
trainer.args

TrainingArguments(output_dir=./gpt2, overwrite_output_dir=True, do_train=False, do_eval=None, do_predict=False, evaluation_strategy=EvaluationStrategy.EPOCH, prediction_loss_only=False, per_device_train_batch_size=8, per_device_eval_batch_size=8, gradient_accumulation_steps=1, eval_accumulation_steps=None, learning_rate=2e-05, weight_decay=0.01, adam_beta1=0.9, adam_beta2=0.999, adam_epsilon=1e-08, max_grad_norm=1.0, num_train_epochs=1, max_steps=-1, lr_scheduler_type=SchedulerType.LINEAR, warmup_steps=0, logging_dir=runs/Mar13_20-52-25_ip-172-31-36-211, logging_first_step=False, logging_steps=500, save_steps=500, save_total_limit=None, no_cuda=False, seed=42, fp16=False, fp16_opt_level=O1, fp16_backend=auto, local_rank=-1, tpu_num_cores=None, tpu_metrics_debug=False, debug=False, dataloader_drop_last=False, eval_steps=500, dataloader_num_workers=0, past_index=-1, run_name=./gpt2, disable_tqdm=False, remove_unused_columns=True, label_names=None, load_best_model_at_end=False, metric_for

In [46]:
trainer.train()

TrainOutput(global_step=22916, training_loss=3.0227071396196297, metrics={'train_runtime': 37247.813, 'train_samples_per_second': 0.615, 'total_flos': 49956286177738752, 'epoch': 1.0})

In [48]:
import os
output_dir = '/home/ubuntu/project/GPT2/gpt2/final'
model_to_save = model.module if hasattr(model, 'module') else model  # Take care of distributed/parallel training
model_to_save.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

('/home/ubuntu/project/GPT2/gpt2/final/tokenizer_config.json',
 '/home/ubuntu/project/GPT2/gpt2/final/special_tokens_map.json',
 '/home/ubuntu/project/GPT2/gpt2/final/vocab.json',
 '/home/ubuntu/project/GPT2/gpt2/final/merges.txt',
 '/home/ubuntu/project/GPT2/gpt2/final/added_tokens.json')

In [50]:
print(trainer.log)

<bound method Trainer.log of <transformers.trainer.Trainer object at 0x7fd31c3859e8>>


In [67]:
#!pip install bertviz

In [44]:
model = AutoModelForCausalLM.from_pretrained("/home/ubuntu/project/GPT2/gpt2/final",output_hidden_states=True)
tokenizer = AutoTokenizer.from_pretrained("/home/ubuntu/project/GPT2/gpt2/final")

In [45]:
inputs = tokenizer.encode(" In 1935 Einstein showed using his equations that light rays cannot travel faster in the bulk if the matter stress energy satisfies the positive energy condition.", return_tensors='pt')
outputs = model(inputs)
attention = outputs[-1]  # Output includes attention weights when output_attentions=True
tokens = tokenizer.convert_ids_to_tokens(inputs[0]) 

In [46]:
from bertviz import head_view
head_view(attention, tokens)

<IPython.core.display.Javascript object>

In [52]:
word_embeddings = model.module.transformer.wte.weight  # Word Token Embeddings 
position_embeddings = model.module.transformer.wpe.weight

In [53]:
torch.set_printoptions(precision=None, threshold=None, edgeitems=None, linewidth=None, profile=None, sci_mode=False)

In [60]:
hep_abstracts.shape

(140500, 4)

In [61]:
iden=hep_abstracts['id'].values
iden[0]

'0704.0015'

In [164]:
import time

In [168]:
text_index

tensor([[  220,   383, 40204,   286,   262, 31094,  2214,   284, 13522,   318,
          6693,    13,   554,   262,   198, 31605, 19482,  7877,    72, 13730,
          3164,  1912,   319,   262,  6306,   453,   880,  4920,   198,  5936,
         13208,  3657,   286,  5186,  3877,   290, 14091, 28462,    11,   262,
         28276, 27490,   198,   533,   262,   976, 40611,   286,   262,  4931,
           393,  8889,   286, 13522,    13,   554,   428,  2565,    11,   198,
           505,   460,   910,   326,   262,  3877,   366,  7266,  2536, 21307,
             1,   290,   262, 28462,   366,  7266,  2536, 21307,     1,   389,
           407,   198, 10745,  2290,  5864,   416,   262, 29973,  2214,  3264,
            13,  2102,    11,   262,   987, 49501,   198, 23395,   777,  7531,
         47294,  1045,    11,  8766,  1143,   355,   262, 43839,   270, 34752,
          8079,  8695,    92,   198,    39,    28,    39,     7,    37,     8,
          1022,   262,   362,    12, 23914,   286,  

In [193]:
model.to(device)

DataParallel(
  (module): GPT2LMHeadModel(
    (transformer): GPT2Model(
      (wte): Embedding(50257, 1024)
      (wpe): Embedding(1024, 1024)
      (drop): Dropout(p=0.1, inplace=False)
      (h): ModuleList(
        (0): Block(
          (ln_1): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (attn): Attention(
            (c_attn): Conv1D()
            (c_proj): Conv1D()
            (attn_dropout): Dropout(p=0.1, inplace=False)
            (resid_dropout): Dropout(p=0.1, inplace=False)
          )
          (ln_2): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (mlp): MLP(
            (c_fc): Conv1D()
            (c_proj): Conv1D()
            (dropout): Dropout(p=0.1, inplace=False)
          )
        )
        (1): Block(
          (ln_1): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
          (attn): Attention(
            (c_attn): Conv1D()
            (c_proj): Conv1D()
            (attn_dropout): Dropout(p=0.1, inplace=False)
    

# Writing word vectors to a file. Once done with that we use the GPT-2 companion file to obtain recommendations # 

### The first word in every line in the file is the arxiv id. The rest is the 1024 dimensional document vector. ### 

In [ ]:
print(time.time())
f = open("abstracts_gpt2_medium.txt", "w")
f1 = open("abstracts_gpt2_medium_last4avg.txt", "w")
for i in range(1000):
    
    
    f.write(f"{iden[i]} ")
    text_index = tokenizer.encode(texttxt[i],return_tensors='pt')
    vector = model.module.transformer.wte.weight[text_index[0],:]
    vecpy=vector.detach().cpu().numpy()
    x=np.average(vecpy,axis=0)
    
    
    text_index.to(device)
    model.to(device)
    outputs=model(text_index)
   
    f1.write(f"{iden[i]} ")
    hidden_states=outputs[2]
    average_layer=(hidden_states[-1]+hidden_states[-2]+hidden_states[-3]+hidden_states[-4])/4
    avg_sentence_embedding = torch.mean(average_layer, dim=1).squeeze()
    y=avg_sentence_embedding.detach().cpu().numpy()
    
    f.write((' '.join(['%0.10f']*x.size)+'\n') % tuple(x))
    f1.write((' '.join(['%0.10f']*y.size)+'\n') % tuple(y))
    if i%1000==0:
        print(i)
f.close()
f1.close()
print(time.time())

In [96]:
text_index = tokenizer.encode(texttxt[i],return_tensors='pt')
text_index.to(device)
model.to(device)
outputs=model(text_index)

In [128]:
outputs[2][24].shape # hidden states

torch.Size([1, 92, 1024])

In [139]:
outputs[1][23][1].shape #past_key_values

torch.Size([1, 16, 92, 64])

In [118]:
outputs[0].shape  # The output

torch.Size([1, 92, 50257])

In [132]:
outputs[-1][23].shape #Attention

torch.Size([1, 16, 92, 92])

In [298]:
np.set_printoptions(suppress=True)

In [299]:
vector.shape

torch.Size([3, 768])

In [168]:
#word_vectors = [w.vector for w in words]

In [173]:
last_hidden_state.shape

torch.Size([1, 9, 50257])

In [203]:
last_hidden_state

tensor([[[-31.7739, -29.6043, -31.0812,  ..., -42.6106, -42.8951, -32.2430],
         [-52.7065, -52.1494, -50.6033,  ..., -60.2021, -59.6126, -54.4564],
         [-47.6894, -48.0426, -45.1419,  ..., -54.7074, -55.7193, -48.3126],
         ...,
         [-63.8637, -63.7969, -60.7487,  ..., -72.9817, -71.3295, -64.2861],
         [-43.4437, -42.7980, -40.7552,  ..., -51.3229, -50.1440, -43.7538],
         [-62.6173, -63.9406, -62.9483,  ..., -70.8145, -69.1537, -60.4832]]],
       device='cuda:0')